In [0]:
import math, sys 
import numpy as np

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm
from os import path
count = 0

from matplotlib.backends.backend_pdf import PdfPages

## The problem
 
There is a biased coin with $p \in (0,1)$, $p\neq \frac12$, probability of getting heads and $q=1-p$ probability of getting tails. 
 
We will start with an initial wealth $x = i \delta$, $i \in \mathbb N$ with $i<m$, with some $m \in \mathbb N$ fixed reasonably large.  

At each turn we choose an action $a\in \{-1,1\}$. 
By choosing $a=1$ we bet that the coin comes up heads and our wealth is increased by $\delta$ if we are correct, decreased by $\delta$ otherwise. 
By choosing $a=-1$ we bet on tails and our wealth is updated accordingly. 

That is, given that $X_{n-1} = x$ and our action $a\in\{-1,1\}$ we have 
$$
\mathbb P(X_n = x + a\delta | X_{n-1} = x, a) = p\,, \quad \mathbb P(X_n = x - a\delta| X_{n-1} = x, a) = q\,. 
$$

The game terminates when either $x=0$ or $x=m \delta$. 
Let $N = \min \{ n\in \mathbb N : X_n = 0 \,\,\,\text{or}\,\,\, X_n = m\delta\}$. 
Our aim is to maximize
$$
J^{\alpha}(x) = \mathbb E \Big[ X^\alpha_N | X_0 = x \Big]
$$
over functions $\alpha = \alpha(x)$ telling what action to choose in each given state.




## Optimal control approach via Bellman equation

Let the value function be
$$
v(x) := \max_\alpha J^\alpha(x)\,.
$$
The Bellman principle states that
$$
v(x) = \max_a \mathbb E\Big[ v (X_1^a) | X_0 = x\Big]\,.
$$

In the simple case above the optimal strategy is clear: if $p<\frac12$ then $\alpha(x) = -1$ is the optimal strategy, 
while if $p > \frac12$ then $\alpha(x) = 1$ is the optimal strategy. 
So we see obtain the linear functional equation
$$
v(x) = p v (x+a\delta) + q v(x-a\delta)\,,\,\,\, v(0) = 0\,,\,\,\, v(m\delta) = m\delta\,.
$$
This can be solved iteratively (value iteration). 

In [5]:
p = 51.0/100.0
delta = 1
m = 3

x_vals = np.linspace(0,delta*m,m)
a_vals = np.linspace(-1,1,2)

# Lookup table for Q
v_new = np.zeros(np.size(x_vals))
v_old = np.zeros(np.size(x_vals))
v_old[0] = 0; v_old[np.size(x_vals)-1] = m*delta

N_iter = 1000;

a = -1;
if p > 0.5:
  a = 1;

tol = 1e-8

for k in range(0,N_iter):
  # update value function
  v_new[0] = 0; v_new[np.size(x_vals)-1] = m*delta
  for i in range(1,np.size(x_vals)-1):
    v  = p*v_old[i+a] + (1-p)*v_old[i-a]
    #print(v)
    v_new[i] = v

  #check for convergence
  err_v = np.abs(v_new - v_old)
  err = np.linalg.norm(err_v)
  if (err < tol):
    print("Converged in %d iterations" % k)
    break;

  #ready for next iteration
  v_old = v_new;
  v_new = np.zeros(np.size(x_vals))


print(v_old[1:m-1])


Converged in 1 iterations
[1.53]


## Action-values or Q-values

Unlike in a control problem setting we don't assume the knowledge of the value of $p$.

For a policy $\alpha = \alpha(x)$ define Q values (or action-values) as: 
$$
Q^\alpha(x,a) := \mathbb E \Big[ J^\alpha(X_1) | X_0 = x, \alpha_0 = a \Big]\,.
$$
We see that this is expected reward for executing action $a$ in state $x$ and then following policy $\alpha$ thereafter. 
At this point we still don't know how this shall be computed.  

## The Q-learning algorithm 

We need to fix the learning rate at each step: $(\gamma_k)_{k\in \mathbb N}$ such that $\gamma_k \in (0,1)$, $\sum_k \gamma_k^2 < \infty$ and $\sum_k \gamma_k = \infty$. We can take $\gamma_k = \frac1k$ to begin with.

We start by making an initial guess for $Q$, call it $Q_0 = Q_0(x,a)$.
The learning proceeds in episodes, where at the $k$-th episode:
1. We are in the state $x_k$ (this can be either the resulting state of a previous episode or one chosen at random).
1. We select and perform action $a_k$ (randomly seems fine).
1. We observe the state we landed in $y_k$, if $y_k = 0$ then set $R_k = 0$ (we lost), if $y_k = m\delta$ then set $R_k = m\delta$ (we won), otherwise we are still in the game and $R_k = V_{k-1}(y_k)$, where
$$
V_{k-1}(y_k) := \max_{b\in A} Q_{k-1}(y_k,b)\,. 
$$
1. We adjust the $Q_{k-1}(x_k,a_k)$ to $Q_k(x_k,a_k)$ using $\gamma_k$ as
$$
Q_k(x_k,a_k) = (1-\gamma_k) Q_{k-1}(x_k,a_k) + \gamma_k R_k
$$
and we leave the remaining values of $Q_k=Q_{k-1}$ in this episode.

That's all. 

## Conclusion

Once (if) the algorithm converges so that $Q^*(x,a) = \lim_{k\to \infty} Q_k(x,a)$ we then have $v^*(x) = \max_a Q^*(x,a)$ for all $x,a$.

In [0]:
#p = 44.0/100.0
#delta = 1
#m = 5

x_vals = np.linspace(0,delta*m,m)
a_vals = np.linspace(-1,1,2)

# Lookup table for Q
Q_0 = np.zeros((np.size(x_vals),np.size(a_vals)))


i_0 = np.random.randint(1,m-1) # includes first but excludes last

def choose_action(Q, i):
    a_idx = np.random.randint(0,2) # will return either 0 or 1
    return int(a_vals[a_idx]),a_idx
    
def update_V(Q,i):
    return np.max(Q[i,:])    
    
N_learnsteps = 10**5

win_count = 0
lose_count = 0

for k in range(1,N_learnsteps+1):
    a, a_idx = choose_action(Q_0,i_0)
    coin = -1+2*int(np.random.binomial(1,p))
    i_1 = i_0 + coin*a
    #print("Old idx: %d, Action: %d, Coin: %d, New idx: %d" % (i_0, a, coin, i_1))
    R = 0
    if (i_1 <= 0):
        # R stays at 0 as set above
        i_1 = np.random.randint(0,m) # gamme ended, learning hasn't so we restart
        lose_count = lose_count + 1
    elif (i_1 >= m-1):
        R = m*delta
        i_1 = np.random.randint(0,m) # gamme ended, learning hasn't so we restart
        # print('Reward %f' % R)
        win_count = win_count + 1
    else:
        R = update_V(Q_0,i_1)
        
    # We adjust Q values
    #print('Reward %f' % R)
    
    #gamma = 1.0/k
    gamma = np.power(1.0/k,0.55)
    #gamma = 1.0/10
    if (i_0 == 0):
      #print('Loosing position at iteration %d' % k)
      Q_0[i_0,a_idx]  = 0
    elif (i_0 == m-1):
      #print('Winning position at iteration %d' % k)
      Q_0[i_0,a_idx]  = m * delta 
    else:   
      Q_0[i_0,a_idx] = (1-gamma)*Q_0[i_0,a_idx] + gamma*R 
    
    # And we get ready for next round
    i_0 = i_1
    #i_0 = np.random.randint(1,m)
    
    
print('Win count: %d, Lose count: %d' % (win_count,lose_count))

Win count: 8517, Lose count: 8351


In [0]:
Q_0

array([[0.        , 0.        ],
       [1.44395548, 4.65082863],
       [5.12334816, 6.25878317],
       [6.41451261, 6.76310919],
       [6.81485198, 6.92786616],
       [6.94621711, 6.98206721],
       [7.        , 7.        ]])

In [0]:
# Let us calculate V^* - the optimal payoff:
V_ast = np.zeros(np.size(x_vals))

for i in range(0,np.size(x_vals)):
    V_ast[i] = np.max(Q_0[i,:])

print("Value from Q-learning")
print(V_ast[1:m-1])

print ("Value exact")
print(v_old[1:m-1])

print("Difference")
print(np.abs(v_old[1:m-1] - V_ast[1:m-1]))
# Let us calculate a^* - the optimal action:
a_ast = np.zeros(np.size(x_vals))

for i in range(0,np.size(x_vals)):
    a_ast[i] = a_vals[np.argmax(Q_0[i,:])]


#print(a_ast[1:m-1])



Value from Q-learning
[4.65082863 6.25878317 6.76310919 6.92786616 6.98206721]
Value exact
[4.6730769  6.23076922 6.74999999 6.92307692 6.98076923]
Difference
[0.02224827 0.02801395 0.0131092  0.00478924 0.00129799]
